# Balanceamento Estrutural

Importando bibliotecas:

In [1]:
import networkx as nx
import socnet as sn

from random import choice, random
from itertools import combinations

Configurando bibliotecas:

In [2]:
sn.node_size = 5
sn.node_color = (255, 255, 255)

sn.edge_width = 1

Definindo constantes:

In [3]:
NUM_NODES = 15

POSITIVE_COLOR = (0, 0, 255)
NEGATIVE_COLOR = (255, 0, 0)

Inicialização da simulação:

In [4]:
def set_edge_color(g, n, m):
    if g.edges[n, m]['signal'] == 1:
        g.edges[n, m]['color'] = POSITIVE_COLOR
    else:
        g.edges[n, m]['color'] = NEGATIVE_COLOR


def build_graph(frac_positives):
    g = nx.complete_graph(NUM_NODES)

    sn.reset_node_colors(g)

    for n, m in g.edges:
        if random() < frac_positives:
            g.edges[n, m]['signal'] = 1
        else:
            g.edges[n, m]['signal'] = -1

        set_edge_color(g, n, m)

    sn.reset_positions(g)

    return g

Passo da simulação:

In [5]:
def invert(g, n, m):
    g.edges[n, m]['signal'] *= -1

    set_edge_color(g, n, m)


def update(g, mec2_weight=1, mec3_weight=1, mec5_weight=1):
    # Inicializa as pressões.

    for n, m in g.edges():
        g.edges[n, m]['pressure'] = 0

    # Para cada tríade.

    for t in combinations(g.nodes, 3):
        # Lista todas as arestas da tríade.
        edges = [(t[0], t[1]), (t[0], t[2]), (t[1], t[2])]

        # Conta quantas arestas são positivas.
        num_positives = sum(g.edges[n, m]['signal'] == 1 for n, m in edges)

        # Duas positivas significa tríade instável.
        if num_positives == 2:
            for n, m in edges:
                if g.edges[n, m]['signal'] == -1:
                    g.edges[n, m]['pressure'] += mec2_weight # Mecanismo 2
                else:
                    g.edges[n, m]['pressure'] += mec3_weight # Mecanismo 3

        # Zero positivas também significa tríade instável.
        elif num_positives == 0:
            for n, m in edges:
                g.edges[n, m]['pressure'] += mec5_weight # Mecanismo 5

    # Obtém a maior pressão.
    pressure = max(g.edges[n, m]['pressure'] for n, m in g.edges)

    # Se for positiva, inverte uma aresta que esteja
    # sob essa pressão, escolhida aleatoriamente, e
    # devolve True para indicar que houve mudança.
    if pressure > 0:
        n, m = choice([(n, m) for n, m in g.edges if g.edges[n, m]['pressure'] == pressure])
        invert(g, n, m)
        return True

    # Se for zero, devolvendo False para indicar que
    # não houve mudança, ou seja, a rede estabilizou.
    return False

Animação da simulação:

In [6]:
g = build_graph(frac_positives = 0.5)

sn.reset_positions(g)

frames = []

while update(g):
    sn.update_positions(g, weight='signal')

    frames.append(sn.generate_frame(g))

print('simulação encerrada, gerando animação...')

sn.show_animation(frames)

simulação encerrada, gerando animação...


Avaliação da simulação:

In [11]:
def number_components(g):
    h = g.copy()

    for n, m in g.edges:
        if g.edges[n, m]['signal'] == -1:
            h.remove_edge(n, m)

    return nx.number_connected_components(h)


print("Numero de Componentes: {0}".format(number_components(g)) )

Numero de Componentes: 2


Analise Do Grafo Inicializado Com 80% De frações Positivas

In [26]:
def initialize(frac_positives, iteractions):
    componentes = []
    frames      = []
    
    for i in range(iteractions):
        
        g = build_graph(frac_positives)

        sn.reset_positions(g)

        frames_aux = []

        while update(g):
            sn.update_positions(g, weight='signal')

            frames_aux.append(sn.generate_frame(g))
        print(frames_aux)

        componentes.append(number_components(g))
        frames = frames_aux
    
    print('simulação encerrada, gerando animação...')
    
    print(len(frames))
    n_components = sum(componentes)/iteractions
    
    return g, n_components, frames

In [27]:
g2, n_components, frames = initialize(0.8, 100)

sn.show_animation(frames)
print("Numero de Componentes: {0}".format(n_components))

[{'data': [{'x': [0.31678007118473694, 0.44696333224325274, None], 'y': [0.8745765711365356, 0.0, None], 'hoverinfo': 'none', 'mode': 'lines', 'line': {'width': 1, 'color': 'rgb(255, 0, 0)'}}, {'x': [0.31678007118473694, 0.6978671402814994, None], 'y': [0.8745765711365356, 0.09665404214116854, None], 'hoverinfo': 'none', 'mode': 'lines', 'line': {'width': 1, 'color': 'rgb(0, 0, 255)'}}, {'x': [0.31678007118473694, 0.48322079543120033, None], 'y': [0.8745765711365356, 1.0, None], 'hoverinfo': 'none', 'mode': 'lines', 'line': {'width': 1, 'color': 'rgb(0, 0, 255)'}}, {'x': [0.31678007118473694, 0.736860496778769, None], 'y': [0.8745765711365356, 0.9319958135154106, None], 'hoverinfo': 'none', 'mode': 'lines', 'line': {'width': 1, 'color': 'rgb(0, 0, 255)'}}, {'x': [0.31678007118473694, 1.0, None], 'y': [0.8745765711365356, 0.6009562623380699, None], 'hoverinfo': 'none', 'mode': 'lines', 'line': {'width': 1, 'color': 'rgb(0, 0, 255)'}}, {'x': [0.31678007118473694, 0.23032965185852863, Non

[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
simulação encerrada, gerando animação...
0


IndexError: list index out of range